<h1>Singapore vs Hong Kong - A Tale of Two Cities</h1>

<h2>Importing basis libraries and installing packages</h2>

In [1]:
import pandas as pd
import numpy as np

In [2]:
import requests # library to handle requests
import random # library for random number generation

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

!conda install -c conda-forge folium=0.5.0 --yes
import folium # plotting library

print('Folium installed')
print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2020.4.5.1 |       hecc5488_0         146 KB  conda-forge
    certifi-2020.4.5.1         |   py36h9f0ad1d_0         151 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    openssl-1.1.1f             |       h516909a_0         2.1 MB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    branca-0.4.0               |             py_0          26 KB  conda-forge
    ------------------------------------------------------------
                       

<h2>Reading csv files containing district and location data for Singapore and Hong Kong</h2>

In [3]:
# The code was removed by Watson Studio for sharing.

District  Latitude   Longitude  \
0         District 01 - Raffles Place, Marina, Cecil  1.283720  103.851239   
1             District 02 - Tanjong Pagar, Chinatown  1.276571  103.845848   
2   District 03 - Tiong Bahru, Alexandra, Queenstown  1.286197  103.825765   
3  District 04 - Mount Faber, Telok Blangah, Harb...  1.267745  103.822485   
4  District 05 - Buona Vista, Pasir Panjang, Clem...  1.292460  103.787773   

   Population  
0         NaN  
1         NaN  
2         NaN  
3         NaN  
4         NaN

<h2>Visualization of the citys' districts on a map</h2>

In [4]:
hk_address = 'Hong Kong'
hk_latitude = 22.302711
hk_longitude = 114.177216
sg_address = 'Singapore'
sg_latitude = 1.3521
sg_longitude = 103.8198

In [5]:
# create map of New York using latitude and longitude values
hk_map = folium.Map(location=[hk_latitude, hk_longitude], zoom_start=10)

# add markers to map
for lat, lng, region, district in zip(hk_districts_data['Latitude'], hk_districts_data['Longitude'], hk_districts_data['Region'], hk_districts_data['District']):
    label = '{}, {}'.format(district, region)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(hk_map)
    
hk_map

In [6]:
# create map of New York using latitude and longitude values
sg_map = folium.Map(location=[sg_latitude, sg_longitude], zoom_start=10)

for lat, lng, district in zip(sg_districts_data['Latitude'], sg_districts_data['Longitude'], sg_districts_data['District']):
    label = '{}'.format(district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(sg_map)
    
sg_map

<h2>Extracting venue information for each district in Hong Kong</h2>

In [7]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [8]:
CLIENT_ID = 'DXOLZNK5E3HB4GQLOFBTMK1KZKZVADQFLFXVXZHRQOHBXKTK' # your Foursquare ID
CLIENT_SECRET = 'UGSJTKYNZOXNZCYPIK0XP2UTADUJZQVFU43VEJDWBALFRSF4' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

# type your answer here
radius = 3000
LIMIT = 300

def getNearbyVenues(names, latitudes, longitudes, city, radius=500):
    
    nearby_venues = pd.DataFrame(columns=['Name', 'Category', 'Latitude', 'Longitude', 'City', 'District', 'District Latitude', 'District Longitude'])
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        
        results = requests.get(url).json()
        venues = results['response']['venues']
        df = json_normalize(venues) # flatten JSON

        filtered_columns = ['name', 'categories', 'location.lat', 'location.lng']
        df = df.loc[:, filtered_columns]

        # filter the category for each row
        df['categories'] = df.apply(get_category_type, axis=1)
        df['City']=city
        df['District']=name
        df['District Latitude']=lat
        df['District Longitude']=lng
        
        # clean columns
        #df.columns = [col.split(".")[-1] for col in df.columns]
        df.rename(columns={"name": "Name", "categories": "Category","location.lat": "Latitude","location.lng": "Longitude"}, inplace=True)
        nearby_venues = nearby_venues.append(df)
          
    return(nearby_venues)

Your credentails:
CLIENT_ID: DXOLZNK5E3HB4GQLOFBTMK1KZKZVADQFLFXVXZHRQOHBXKTK
CLIENT_SECRET:UGSJTKYNZOXNZCYPIK0XP2UTADUJZQVFU43VEJDWBALFRSF4


In [10]:
hk_venues = getNearbyVenues(names=hk_districts_data['District'],
                                   latitudes=hk_districts_data['Latitude'],
                                   longitudes=hk_districts_data['Longitude'],
                                   city="Hong Kong"
                                  )
hk_venues.head()

Central and Western
Eastern
Southern
Wan Chai
Sham Shui Po
Kowloon City
Kwun Tong
Wong Tai Sin
Yau Tsim Mong
Islands
Kwai Tsing
North
Sai Kung
Sha Tin
Tai Po
Tsuen Wan
Tuen Mun
Yuen Long


Name              Category  \
0  Immigration Department Travel Documents Issuin...   Government Building   
1                          Harbour Building (海港政府大樓)   Government Building   
2                              Marine Department 海事處   Government Building   
3                            Infinitus Plaza (無限極廣場)         Shopping Mall   
4                             Fitness First Platinum  Gym / Fitness Center   

    Latitude   Longitude       City             District  District Latitude  \
0  22.286864  114.155123  Hong Kong  Central and Western           22.28666   
1  22.286592  114.154997  Hong Kong  Central and Western           22.28666   
2  22.286571  114.154943  Hong Kong  Central and Western           22.28666   
3  22.286463  114.153689  Hong Kong  Central and Western           22.28666   
4  22.285881  114.154117  Hong Kong  Central and Western           22.28666   

   District Longitude  
0           114.15497  
1           114.15497  
2           114.15497  
3           114.15497  
4           114.15497

In [11]:
hk_venues.size

15824

<h2>Extracting venue information for each district in Singapore</h2>

In [12]:
sg_venues = getNearbyVenues(names=sg_districts_data['District'],
                                   latitudes=sg_districts_data['Latitude'],
                                   longitudes=sg_districts_data['Longitude'],
                                   city="Singapore"
                                  )
sg_venues.head()

District 01 - Raffles Place, Marina, Cecil
District 02 - Tanjong Pagar, Chinatown
District 03 - Tiong Bahru, Alexandra, Queenstown
District 04 - Mount Faber, Telok Blangah, Harbourfront
District 05 - Buona Vista, Pasir Panjang, Clementi
District 06 - Clarke Quay, City Hall
District 07 - Bugis, Beach Road, Golden Mile
District 08 - Little India, Farrer Park
District 09 - Orchard Road, River Valley
District 10 - Bukit Timah, Holland, Balmoral
District 11 - Novena, Newton, Thomson
District 12 - Toa Payoh, Serangoon, Balestier
District 13 - Macpherson, Braddell
District 14 - Geylang, Paya Lebar, Sims
District 15 - Joo Chiat, Marina Parade, Katong
District 16 - Bedok, Upper East Coast, Siglap
District 17 - Changi, Flora, Loyang
District 18 - Tampines, Pasir Ris
District 19 - Punggol, Sengkang, Serangoon Gardens
District 20 - Ang Mo Kio, Bishan, Thomson
District 21 - Upper Bukit Timah, Ulu Pandan, Clementi Park
District 22 - Boon Lay, Jurong, Tuas
District 23 - Choa Chu Kang, Diary Farm, Hil

Name                    Category  Latitude   Longitude  \
0  Arcade Money Changers           Currency Exchange  1.283997  103.851197   
1        Clifford Centre                      Office  1.283816  103.852219   
2    City Money Changers  Financial or Legal Service  1.283475  103.850161   
3        In Touch Physio              Medical Center  1.283503  103.851163   
4             The Arcade               Shopping Mall  1.283746  103.851718   

        City                                    District  District Latitude  \
0  Singapore  District 01 - Raffles Place, Marina, Cecil            1.28372   
1  Singapore  District 01 - Raffles Place, Marina, Cecil            1.28372   
2  Singapore  District 01 - Raffles Place, Marina, Cecil            1.28372   
3  Singapore  District 01 - Raffles Place, Marina, Cecil            1.28372   
4  Singapore  District 01 - Raffles Place, Marina, Cecil            1.28372   

   District Longitude  
0          103.851239  
1          103.851239  
2          103.851239  
3          103.851239  
4          103.851239

In [13]:
sg_venues.size

26800

<h2>Some pre-analysis of data</h2>

In [14]:
hk_venues.groupby('Category').count()
print('There are {} uniques categories of venues in Hong Kong.'.format(len(hk_venues['Category'].unique())))

There are 304 uniques categories of venues in Hong Kong.


In [15]:
sg_venues.groupby('Category').count()
print('There are {} uniques categories of venues in Singapore.'.format(len(sg_venues['Category'].unique())))

There are 386 uniques categories of venues in Singapore.


In [16]:
#Combining the two dataframes
all_venues = hk_venues.append(sg_venues)
all_venues.head()
all_venues.size

42624

In [18]:
# one hot encoding
all_onehot = pd.get_dummies(all_venues[['Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
all_onehot['District'] = all_venues['District'] 

# move neighborhood column to the first column
fixed_columns = [all_onehot.columns[-1]] + list(all_onehot.columns[:-1])
all_onehot = all_onehot[fixed_columns]

all_onehot.head()

District  ATM  Accessories Store  Acupuncturist  \
0  Central and Western    0                  0              0   
1  Central and Western    0                  0              0   
2  Central and Western    0                  0              0   
3  Central and Western    0                  0              0   
4  Central and Western    0                  0              0   

   Adult Education Center  Advertising Agency  African Restaurant  Airport  \
0                       0                   0                   0        0   
1                       0                   0                   0        0   
2                       0                   0                   0        0   
3                       0                   0                   0        0   
4                       0                   0                   0        0   

   Airport Gate  Airport Lounge  ...  Waterfront  Well  Wine Bar  Wine Shop  \
0             0               0  ...           0     0         0          0   
1             0               0  ...           0     0         0          0   
2             0               0  ...           0     0         0          0   
3             0               0  ...           0     0         0          0   
4             0               0  ...           0     0         0          0   

   Winery  Wings Joint  Women's Store  Yoga Studio  Yunnan Restaurant  \
0       0            0              0            0                  0   
1       0            0              0            0                  0   
2       0            0              0            0                  0   
3       0            0              0            0                  0   
4       0            0              0            0                  0   

   Zoo Exhibit  
0            0  
1            0  
2            0  
3            0  
4            0  

[5 rows x 452 columns]

In [19]:
all_grouped = all_onehot.groupby('District').mean().reset_index()
all_grouped

District       ATM  \
0                                 Central and Western  0.000000   
1          District 01 - Raffles Place, Marina, Cecil  0.000000   
2              District 02 - Tanjong Pagar, Chinatown  0.000000   
3    District 03 - Tiong Bahru, Alexandra, Queenstown  0.000000   
4   District 04 - Mount Faber, Telok Blangah, Harb...  0.000000   
5   District 05 - Buona Vista, Pasir Panjang, Clem...  0.000000   
6                District 06 - Clarke Quay, City Hall  0.000000   
7        District 07 - Bugis, Beach Road, Golden Mile  0.000000   
8             District 08 - Little India, Farrer Park  0.000000   
9            District 09 - Orchard Road, River Valley  0.000000   
10       District 10 - Bukit Timah, Holland, Balmoral  0.000000   
11              District 11 - Novena, Newton, Thomson  0.000000   
12      District 12 - Toa Payoh, Serangoon, Balestier  0.000000   
13                 District 13 - Macpherson, Braddell  0.000000   
14            District 14 - Geylang, Paya Lebar, Sims  0.000000   
15     District 15 - Joo Chiat, Marina Parade, Katong  0.000000   
16      District 16 - Bedok, Upper East Coast, Siglap  0.000000   
17                District 17 - Changi, Flora, Loyang  0.000000   
18                  District 18 - Tampines, Pasir Ris  0.000000   
19  District 19 - Punggol, Sengkang, Serangoon Gar...  0.008264   
20          District 20 - Ang Mo Kio, Bishan, Thomson  0.000000   
21  District 21 - Upper Bukit Timah, Ulu Pandan, C...  0.000000   
22               District 22 - Boon Lay, Jurong, Tuas  0.000000   
23  District 23 - Choa Chu Kang, Diary Farm, Hillv...  0.007752   
24         District 24 - Kranji, Lim Chu Kang, Tengah  0.000000   
25                 District 25 - Woodlands, Admiralty  0.023438   
26                District 26 - Upper Thomson, Mandai  0.000000   
27         District 27 - Sembawang, Yishun, Admiralty  0.007937   
28                District 28 - Yio Chu Kang, Seletar  0.000000   
29                                            Eastern  0.008197   
30                                            Islands  0.000000   
31                                       Kowloon City  0.000000   
32                                         Kwai Tsing  0.000000   
33                                          Kwun Tong  0.007937   
34                                              North  0.000000   
35                                           Sai Kung  0.000000   
36                                            Sha Tin  0.000000   
37                                       Sham Shui Po  0.008065   
38                                           Southern  0.000000   
39                                             Tai Po  0.000000   
40                                          Tsuen Wan  0.008333   
41                                           Tuen Mun  0.000000   
42                                           Wan Chai  0.000000   
43                                       Wong Tai Sin  0.000000   
44                                      Yau Tsim Mong  0.000000   
45                                          Yuen Long  0.000000   

    Accessories Store  Acupuncturist  Adult Education Center  \
0            0.000000       0.000000                0.011111   
1            0.000000       0.000000                0.000000   
2            0.000000       0.000000                0.000000   
3            0.000000       0.007937                0.000000   
4            0.008333       0.000000                0.000000   
5            0.000000       0.000000                0.000000   
6            0.000000       0.000000                0.000000   
7            0.007576       0.000000                0.000000   
8            0.000000       0.000000                0.000000   
9            0.000000       0.000000                0.000000   
10           0.000000       0.000000                0.000000   
11           0.000000       0.000000                0.000000   
12           0.000000       0.009615                0.000000   

In [20]:
all_grouped.shape

(46, 452)

In [21]:
num_top_venues = 5

for hood in all_grouped['District']:
    print("----"+hood+"----")
    temp = all_grouped[all_grouped['District'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Central and Western----
                 venue  freq
0             Building  0.08
1  Government Building  0.06
2               Office  0.04
3      Doctor's Office  0.04
4          Coffee Shop  0.03


----District 01 - Raffles Place, Marina, Cecil----
         venue  freq
0       Office  0.07
1       Bakery  0.06
2     Building  0.04
3         Bank  0.04
4  Salad Place  0.04


----District 02 - Tanjong Pagar, Chinatown----
                 venue  freq
0  Japanese Restaurant  0.10
1               Office  0.06
2                 Café  0.05
3          Coffee Shop  0.05
4     Asian Restaurant  0.03


----District 03 - Tiong Bahru, Alexandra, Queenstown----
                venue  freq
0            Building  0.06
1   College Classroom  0.06
2         Coffee Shop  0.05
3    Asian Restaurant  0.03
4  Chinese Restaurant  0.03


----District 04 - Mount Faber, Telok Blangah, Harbourfront----
                venue  freq
0      Clothing Store  0.03
1              Office  0.03
2  Chinese Restauran

In [22]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [23]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['District']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
district_venues_sorted = pd.DataFrame(columns=columns)
district_venues_sorted['District'] = all_grouped['District']

for ind in np.arange(all_grouped.shape[0]):
    district_venues_sorted.iloc[ind, 1:] = return_most_common_venues(all_grouped.iloc[ind, :], num_top_venues)

district_venues_sorted.head()

District 1st Most Common Venue  \
0                                Central and Western              Building   
1         District 01 - Raffles Place, Marina, Cecil                Office   
2             District 02 - Tanjong Pagar, Chinatown   Japanese Restaurant   
3   District 03 - Tiong Bahru, Alexandra, Queenstown     College Classroom   
4  District 04 - Mount Faber, Telok Blangah, Harb...        Clothing Store   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0   Government Building       Doctor's Office                Office   
1                Bakery                  Bank              Building   
2                Office                  Café           Coffee Shop   
3              Building           Coffee Shop    Chinese Restaurant   
4    Chinese Restaurant                Office        Cosmetics Shop   

                      5th Most Common Venue 6th Most Common Venue  \
0                                  Bus Stop       Coworking Space   
1                                      Café           Salad Place   
2                                  Building        Sandwich Place   
3  Residential Building (Apartment / Condo)      Asian Restaurant   
4                             Jewelry Store            Food Court   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                   Lawyer      Dentist's Office  Gym / Fitness Center   
1  Health & Beauty Service        Medical Center   Japanese Restaurant   
2         Asian Restaurant    Chinese Restaurant        Cosmetics Shop   
3               Food Court      Dentist's Office        Medical Center   
4                 Boutique                  Café   Sporting Goods Shop   

  10th Most Common Venue  
0            Coffee Shop  
1       Asian Restaurant  
2                   Park  
3             Nail Salon  
4    Housing Development

<h2>Now we will cluster the districts from both cities</h2>

In [24]:
# import k-means from clustering stage
from sklearn.cluster import KMeans

# set number of clusters
kclusters = 4

all_grouped_clustering = all_grouped.drop('District', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(all_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 3, 0, 3, 3, 2, 3, 0, 3, 2], dtype=int32)

In [25]:
# add clustering labels
district_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

all_merged = all_venues

# merge to add latitude/longitude for each neighborhood
all_merged = all_merged.join(district_venues_sorted.set_index('District'), on='District')

all_merged.head() # check the last columns!

Name              Category  \
0  Immigration Department Travel Documents Issuin...   Government Building   
1                          Harbour Building (海港政府大樓)   Government Building   
2                              Marine Department 海事處   Government Building   
3                            Infinitus Plaza (無限極廣場)         Shopping Mall   
4                             Fitness First Platinum  Gym / Fitness Center   

    Latitude   Longitude       City             District  District Latitude  \
0  22.286864  114.155123  Hong Kong  Central and Western           22.28666   
1  22.286592  114.154997  Hong Kong  Central and Western           22.28666   
2  22.286571  114.154943  Hong Kong  Central and Western           22.28666   
3  22.286463  114.153689  Hong Kong  Central and Western           22.28666   
4  22.285881  114.154117  Hong Kong  Central and Western           22.28666   

   District Longitude  Cluster Labels 1st Most Common Venue  \
0           114.15497               3              Building   
1           114.15497               3              Building   
2           114.15497               3              Building   
3           114.15497               3              Building   
4           114.15497               3              Building   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0   Government Building       Doctor's Office                Office   
1   Government Building       Doctor's Office                Office   
2   Government Building       Doctor's Office                Office   
3   Government Building       Doctor's Office                Office   
4   Government Building       Doctor's Office                Office   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0              Bus Stop       Coworking Space                Lawyer   
1              Bus Stop       Coworking Space                Lawyer   
2              Bus Stop       Coworking Space                Lawyer   
3              Bus Stop       Coworking Space                Lawyer   
4              Bus Stop       Coworking Space                Lawyer   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0      Dentist's Office  Gym / Fitness Center            Coffee Shop  
1      Dentist's Office  Gym / Fitness Center            Coffee Shop  
2      Dentist's Office  Gym / Fitness Center            Coffee Shop  
3      Dentist's Office  Gym / Fitness Center            Coffee Shop  
4      Dentist's Office  Gym / Fitness Center            Coffee Shop

<h2>Let's visualize our cluster on the map (please zoom in to see all the clusters in the two cities)</h2>

In [26]:
import matplotlib.cm as cm
import matplotlib.colors as colors
# create map
map_clusters = folium.Map(location=[hk_latitude, hk_longitude], zoom_start=2)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(all_merged['District Latitude'], all_merged['District Longitude'], all_merged['District'], all_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<h2>Now let's take a look at the clusters formed and analyze them</h2>

In [51]:
c1 = all_merged.loc[all_merged['Cluster Labels'] == 0, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]
c11 = c1.groupby('District').count()
c1

Category                             District  \
0                      Courthouse                              Eastern   
1             Housing Development                              Eastern   
2                     Bus Station                              Eastern   
3                  Police Station                              Eastern   
4                            Park                              Eastern   
5                   Grocery Store                              Eastern   
6                          Market                              Eastern   
7                            Park                              Eastern   
8             Housing Development                              Eastern   
9                            Pier                              Eastern   
10           Hong Kong Restaurant                              Eastern   
11                     Courthouse                              Eastern   
12                         Bakery                              Eastern   
13                    Coffee Shop                              Eastern   
14                Laundry Service                              Eastern   
15                        Stadium                              Eastern   
16           Fast Food Restaurant                              Eastern   
17                         Bakery                              Eastern   
18                  Hot Dog Joint                              Eastern   
19                Laundry Service                              Eastern   
20                    Pizza Place                              Eastern   
21               Sushi Restaurant                              Eastern   
22                        Parking                              Eastern   
23             Chinese Restaurant                              Eastern   
24                        Library                              Eastern   
25                Harbor / Marina                              Eastern   
26                 Medical Center                              Eastern   
27                      Juice Bar                              Eastern   
28            Japanese Restaurant                              Eastern   
29                           Park                              Eastern   
..                            ...                                  ...   
69               Asian Restaurant  District 26 - Upper Thomson, Mandai   
70                Automotive Shop  District 26 - Upper Thomson, Mandai   
71                      Pet Store  District 26 - Upper Thomson, Mandai   
72                    Supermarket  District 26 - Upper Thomson, Mandai   
73                      Bike Shop  District 26 - Upper Thomson, Mandai   
74                Automotive Shop  District 26 - Upper Thomson, Mandai   
75                Automotive Shop  District 26 - Upper Thomson, Mandai   
76                Automotive Shop  District 26 - Upper Thomson, Mandai   
77                          Diner  District 26 - Upper Thomson, Mandai   
78                  Military Base  District 26 - Upper Thomson, Mandai   
79             Chinese Restaurant  District 26 - Upper Thomson, Mandai   
80              Korean Restaurant  District 26 - Upper Thomson, Mandai   
81                    Coffee Shop  District 26 - Upper Thomson, Mandai   
82                    Coffee Shop  District 26 - Upper Thomson, Mandai   
83  Vegetarian / Vegan Restaurant  District 26 - Upper Thomson, Mandai   
84                         Arcade  District 26 - Upper Thomson, Mandai   
85            Housing Development  District 26 - Upper Thomson, Mandai   
86              Indian Restaurant  District 26 - Upper Thomson, Mandai   
87                     Strip Club  District 26 - Upper Thomson, Mandai   
88               Asian Restaurant  District 26 - Upper Thomson, Mandai   
89                         Resort  District 26 - Upper Thomson, Mandai   
90               Asian Restaurant  District 26 - Upper Thomson, Mandai   
91               Asian Restau

In [47]:
c2 = all_merged.loc[all_merged['Cluster Labels'] == 1, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]
c22 = c2.groupby('District').count()
c22

Category  District Latitude  District Longitude  Cluster Labels  \
District                                                                        
Kowloon City       115                121                 121             121   

              1st Most Common Venue  2nd Most Common Venue  \
District                                                     
Kowloon City                    121                    121   

              3rd Most Common Venue  4th Most Common Venue  \
District                                                     
Kowloon City                    121                    121   

              5th Most Common Venue  6th Most Common Venue  \
District                                                     
Kowloon City                    121                    121   

              7th Most Common Venue  8th Most Common Venue  \
District                                                     
Kowloon City                    121                    121   

              9th Most Common Venue  10th Most Common Venue  
District                                                     
Kowloon City                    121                     121

In [48]:
c3 =all_merged.loc[all_merged['Cluster Labels'] == 2, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]
c33 = c3.groupby('District').count()
c33

Category  \
District                                                       
District 05 - Buona Vista, Pasir Panjang, Clementi       107   
District 09 - Orchard Road, River Valley                 112   
Wan Chai                                                 119   

                                                    District Latitude  \
District                                                                
District 05 - Buona Vista, Pasir Panjang, Clementi                124   
District 09 - Orchard Road, River Valley                          126   
Wan Chai                                                          125   

                                                    District Longitude  \
District                                                                 
District 05 - Buona Vista, Pasir Panjang, Clementi                 124   
District 09 - Orchard Road, River Valley                           126   
Wan Chai                                                           125   

                                                    Cluster Labels  \
District                                                             
District 05 - Buona Vista, Pasir Panjang, Clementi             124   
District 09 - Orchard Road, River Valley                       126   
Wan Chai                                                       125   

                                                    1st Most Common Venue  \
District                                                                    
District 05 - Buona Vista, Pasir Panjang, Clementi                    124   
District 09 - Orchard Road, River Valley                              126   
Wan Chai                                                              125   

                                                    2nd Most Common Venue  \
District                                                                    
District 05 - Buona Vista, Pasir Panjang, Clementi                    124   
District 09 - Orchard Road, River Valley                              126   
Wan Chai                                                              125   

                                                    3rd Most Common Venue  \
District                                                                    
District 05 - Buona Vista, Pasir Panjang, Clementi                    124   
District 09 - Orchard Road, River Valley                              126   
Wan Chai                                                              125   

                                                    4th Most Common Venue  \
District                                                                    
District 05 - Buona Vista, Pasir Panjang, Clementi                    124   
District 09 - Orchard Road, River Valley                              126   
Wan Chai                                                              125   

                                                    5th Most Common Venue  \
District                                                                    
District 05 - Buona Vista, Pasir Panjang, Clementi                    124   
District 09 - Orchard Road, River Valley                              126   
Wan Chai                                                              125   

                                                    6th Most Common Venue  \
District                                                                    
District 05 - Buona Vista, Pasir Panjang, Clementi                    124   
District 09 - Orchard Road, River Valley                              126   
Wan Chai                                                              125   

                                                    7th Most Common Venue  \
District                                                                    
District 05 - Buona Vista, Pasir Panjang, Clementi                    124   
District 09 - Orchard Road, River Valley                              126   
Wan Chai           

In [50]:
c4 = all_merged.loc[all_merged['Cluster Labels'] == 3, all_merged.columns[[1] + list(range(5, all_merged.shape[1]))]]
c44 = c4.groupby('District').count()
c4

Category  \
0                         Government Building   
1                         Government Building   
2                         Government Building   
3                               Shopping Mall   
4                        Gym / Fitness Center   
5                               Travel Lounge   
6                               Boat or Ferry   
7                                    Heliport   
8                             Coworking Space   
9                                 Coffee Shop   
10                               Burger Joint   
11                                 Steakhouse   
12                              Travel Agency   
13                                   Building   
14                                     Bakery   
15              Vegetarian / Vegan Restaurant   
16                                   Building   
17                                  Juice Bar   
18                                Flea Market   
19                              Jewelry Store   
20                       Fast Food Restaurant   
21                               Noodle House   
22                                   Bus Stop   
23                                       Café   
24                                     Bakery   
25                                   Building   
26                               Tech Startup   
27                                   Building   
28                             Cosmetics Shop   
29                                     Office   
..                                        ...   
91                       Arts & Entertainment   
92                       Gym / Fitness Center   
93                                   Gym Pool   
94   Residential Building (Apartment / Condo)   
95   Residential Building (Apartment / Condo)   
96                          Indian Restaurant   
97   Residential Building (Apartment / Condo)   
98                                       None   
99                                    Parking   
100                             Military Base   
101                            History Museum   
102                                    Office   
103                             Military Base   
104                                       Gym   
105                                  Bus Stop   
106                            Breakfast Spot   
107                            Breakfast Spot   
108                           Other Nightlife   
109                                 Rest Area   
110                                Hotel Pool   
111                               Art Gallery   
112  Residential Building (Apartment / Condo)   
113                                    Resort   
114                                  Bus Stop   
115                               Art Gallery   
116                            Student Center   
117  Residential Building (Apartment / Condo)   
118                               Event Space   
119  Residential Building (Apartment / Condo)   
120                                 Hotel Bar   

                                District  District Latitude  \
0                    Central and Western          22.286660   
1                    Central and Western          22.286660   
2                    Central and Western          22.286660   
3                    Central and Western          22.286660   
4                    Central and Western          22.286660   
5                    Central and Western          22.286660   
6                    Central and Western          22.286660   
7                    Central and Western          22.286660   
8                    Central and Western          22.286660   
9                    Central and Western          22.286660   
10                   Central and Western          22.286660   
11                   Central and Western          22.286660   
12                   Central and Western          22.286660   
13                   Central and Western          22.286660   
14                   Central and Western          22.